In [1]:
%cd ../..
from inference import StyleTTS2, Diffusion

import librosa
import IPython.display as ipd
import torch.cuda

device = 'cuda' if torch.cuda.is_available() else 'cpu'
#device = 'cpu'

d:\Project\TTS\Experimental\StyleTTS2-lite


[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\catto\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


### Load G2P

If you did not use eSpeak for your language, please add your own G2P.

In [2]:
import sys
import phonemizer
if sys.platform.startswith("win"):
    try:
        from phonemizer.backend.espeak.wrapper import EspeakWrapper
        import espeakng_loader
        EspeakWrapper.set_library(espeakng_loader.get_library_path())
    except Exception as e:
        print(e)

def get_phoneme(text, lang):
    try:
        my_phonemizer = phonemizer.backend.EspeakBackend(language=lang, preserve_punctuation=True,  with_stress=True, language_switch='remove-flags')
        return my_phonemizer.phonemize([text])[0]
    except Exception as e:
        print(e)

### Load models

In [3]:
config_path = "Configs/config.yaml"
models_path = "Models/Finetune/mix_200k.pth"

config_diff_path = "Configs/config_diff.yaml"
models_diff_path = "Models/Finetune/current_diffusion.pth"

### Synthesize speech

Little Note: Reference audio has a huge impact on the result. It is best to select audio around 10s long and consistent in both tone and speed.

In [4]:
speaker = {
    "path": "./Demo/Audio/17_santa.wav",  #Ref audio path
    "speed": 1.0,                        #Speaking speed
}

max_samples = 24000*20 #max 20 seconds ref audio
print(speaker['path'])
wave, sr = librosa.load(speaker['path'], sr=24000)
audio, index = librosa.effects.trim(wave, top_db=30)
if sr != 24000:              audio = librosa.resample(audio, sr, 24000)
if len(audio) > max_samples: audio = audio[:max_samples]
display(ipd.Audio(audio, rate=24000, normalize=True))

./Demo/Audio/17_santa.wav


In [5]:
text = '''
Đây là chuyến thăm Việt Nam đầu tiên của Tổng thống Emmanuel Macron kể từ khi ông nhậm chức vào năm 2017 và tái đắc cử vào năm 2022. Chuyến thăm của Tổng thống Pháp Emmanuel Macron thể hiện sự coi trọng và cam kết mạnh mẽ của lãnh đạo cấp cao Pháp đối với việc củng cố và phát triển quan hệ với Việt Nam, đưa quan hệ Đối tác Chiến lược Toàn diện đi vào thực chất và hiệu quả.

Đoàn xe chở Tổng thống Pháp Emmanuel Macron và Phu nhân tiến vào Phủ Chủ tịch trong sự chào mừng nồng nhiệt của đông đảo các em học sinh Thủ đô với lá cờ hai nước trên tay. Chủ tịch nước Lương Cường và Phu nhân đón Tổng thống Pháp Emmanuel Macron và Phu nhân tại nơi đỗ xe, bắt tay nhiệt liệt chào mừng Tổng thống Pháp thăm cấp Nhà nước tới Việt Nam.
'''

| Parameter      | Type   | Description                                                                 | Performance Impact                                |
|----------------|--------|-----------------------------------------------------------------------------|----------------------------------------------------|
| `avg_style`     | BOOL   | Split the reference audio and calculate the average speaking style.        | Higher computation during style extraction         |
| `denoise`       | FLOAT  | Adjusts denoiser strength; range [0, 1].                                   | Additional computation for style processing        |
| `stabilize`     | BOOL   | Stabilizes speaking speed for long-form synthesis.                         | Slight additional computation                      |
| `n_merge`       | INT    | Avoids short sentences by merging if words < `n_merge`.                   | Higher VRAM usage as value increases               |


In [14]:
model = StyleTTS2(config_path, 
                  models_path,
                  # config_diff_path, 
                  # models_diff_path
                ).eval().to(device)


Found: 189 symbols
decoder : 54289492
predictor : 16194612
text_encoder : 5612032
style_encoder : 13845440

Total : 89941576


In [ ]:
avg_style         = False
denoise           = 0.0
stabilize         = False    
n_merge           = 20
steps             = 14
embedding_scale   = 1
with torch.no_grad():
    phonemes = get_phoneme(text=text, lang="vi")
    styles  = model.get_styles(speaker, denoise, avg_style)
    r       = model.generate(phonemes, styles, steps, embedding_scale, n_merge, stabilize)

print('Synthesized:')
display(ipd.Audio(r, rate=24000, normalize=True))

Computing the style for: ./Demo/Audio/17_santa.wav
Generating Audio...
Synthesized:


In [ ]:
# avg_style         = False
# denoise           = 0.0
# stabilize         = False    
# n_merge           = 20
# with torch.no_grad():
#     phonemes = get_phoneme(text=text, lang="vi")
#     styles  = model.get_styles(speaker, denoise, avg_style)
#     r       = model.generate(phonemes, styles, n_merge, stabilize)

# print('Synthesized:')
# display(ipd.Audio(r, rate=24000, normalize=True))

Computing the style for: ./Demo/Audio/17_santa.wav
Generating Audio...
Synthesized:


Optional: The styles tensor can be saved and re-use later for faster generation time.

In [8]:
# model.save_styles(save_dir="./style1.pt")
# model.load_styles(save_dir="./style1.pt")

In [9]:
# with torch.no_grad():
#     phonemes = get_phoneme(text=text, lang="en-us")
#     styles  = model.get_styles(speaker, load_styles=True)
#     r       = model.generate(phonemes, styles, stabilize, n_merge)

# print('Synthesized:')
# display(ipd.Audio(r, rate=24000, normalize=True))